# Data Exploration

The idea of this notebook is to explore the data in the satelite images that come in. Aim to explore the different channels of the satelite data as well and understand the strcuture of the data produced by the 'data generator'. 

*Unclear if this work has been done before, but still useful to explore the data for myself

In [4]:
import os
from nowcasting_dataset.dataset import NetCDFDataset, SAT_VARIABLE_NAMES
import plotly.graph_objects as go
import plotly
import pandas as pd
import numpy as np

DATA_PATH = 'gs://solar-pv-nowcasting-data/prepared_ML_training_data/v4/'
TEMP_PATH = '.'

In [6]:
# set up data generator

train_dataset = NetCDFDataset(
    24_900,
    os.path.join(DATA_PATH, 'train'),
    os.path.join(TEMP_PATH, 'train'))

train_dataset.per_worker_init(1)
train_dataset_iterator = iter(train_dataset)

/Users/peterdudfield/miniconda3/envs/nowcasting_dataset/lib/python3.9/site-packages/google/auth/_default.py:70: UserWarning: Your application has authenticated using end user credentials from Google Cloud SDK without a quota project. You might receive a "quota exceeded" or "API not enabled" error. We recommend you rerun `gcloud auth application-default login` and make sure a quota project is added. Or you can use service accounts instead. For more information about service accounts, see https://cloud.google.com/docs/authentication/
  warnings.warn(_CLOUD_SDK_CREDENTIALS_WARNING)


In [7]:
# get batch of data, this may take a few seconds to run
data = next(train_dataset_iterator)

In [8]:
# get the timestamp of the image
sat_datetime = pd.to_datetime(data['sat_datetime_index'][6, 0],unit='s')
print(sat_datetime)

x_coordinates = data['sat_x_coords'][6]
x_max = np.max(x_coordinates)
x_min = np.min(x_coordinates)
print(x_coordinates)
print(x_min, x_max)

y_coordinates = data['sat_y_coords'][6]
y_max = np.max(y_coordinates)
y_min = np.min(y_coordinates)
print(y_coordinates)
print(y_min, y_max)




2019-05-17 04:55:00
[484000 486000 488000 490000 492000 494000 496000 498000 500000 502000
 504000 506000 508000 510000 512000 514000 516000 518000 520000 522000
 524000 526000 528000 530000 532000 534000 536000 538000 540000 542000
 544000 546000 548000 550000 552000 554000 556000 558000 560000 562000
 564000 566000 568000 570000 572000 574000 576000 578000 580000 582000
 584000 586000 588000 590000 592000 594000 596000 598000 600000 602000
 604000 606000 608000 610000]
484000 610000
[326000 324000 322000 320000 318000 316000 314000 312000 310000 308000
 306000 304000 302000 300000 298000 296000 294000 292000 290000 288000
 286000 284000 282000 280000 278000 276000 274000 272000 270000 268000
 266000 264000 262000 260000 258000 256000 254000 252000 250000 248000
 246000 244000 242000 240000 238000 236000 234000 232000 230000 228000
 226000 224000 222000 220000 218000 216000 214000 212000 210000 208000
 206000 204000 202000 200000]
200000 326000


In [9]:
# make long and lat

from nowcasting_dataset.geospatial import osgb_to_lat_lon

lat_min, lon_min = osgb_to_lat_lon(x=x_min,y=y_min)
lat_max, lon_max = osgb_to_lat_lon(x=x_max,y=y_max)

print(lat_min,lon_min)
print(lat_max,lon_max)

51.69248145276831 -0.7861138648355228
52.790712450447494 1.1130330977481062


In [37]:
# get satelite image

import staticmaps

osm = staticmaps.tile_provider_OSM
osm.tile_size=256

context = staticmaps.Context()
context.set_tile_provider(osm)

frankfurt = staticmaps.create_latlng(51.69, 1.14)
newyork = staticmaps.create_latlng(55.79, 1.15)


# context.add_object(staticmaps.Line([frankfurt, newyork], color=staticmaps.BLUE, width=4))
context.add_object(staticmaps.Marker(frankfurt, color=staticmaps.GREEN, size=12))
context.add_object(staticmaps.Marker(newyork, color=staticmaps.RED, size=12))

print(context.determine_center_zoom(1000,1000))
print(context._tile_provider.tile_size())


image = context.render_pillow(1000, 1000)
image.save("frankfurt_newyork.pillow.png")

TypeError: 'int' object is not callable

In [11]:
print(download_obj)

In [23]:

# image of first channel, the 'HRV' channel
image_inex=6
z = data['sat_data'][image_index][0][:, :, 0]

# plot image
fig = go.Figure(data=
go.Contour(
    z=z
))

fig.show()

In [20]:
# plot all channels
image_index = 6
total_channels = 12

from plotly.subplots import make_subplots


N_cols = 4
N_rows = 3
fig = make_subplots(rows=N_rows, cols=N_cols, subplot_titles=SAT_VARIABLE_NAMES)


# loop over the channels and plot them
for channel in range(0, total_channels):
    
    row = channel % N_rows + 1
    col = channel // N_rows + 1
    
    z = data['sat_data'][image_index][0][:, :, channel]
    
    fig.add_trace(go.Heatmap(z=z, showscale=False),row=row, col=col)

fig.update_layout(height=600, width=800, title_text="Satelite Images Channel plots")
fig.show()

In [21]:
# make little video
image_index=6
channel_index=0

frames = []

# loop over frames for different times
for frame in range(0,19):

    z = data['sat_data'][image_index][frame][:, :, channel_index]
    frames.append(go.Frame(data=[go.Heatmap(z=z, showscale=False)]))

# make first frame   
z0 = data['sat_data'][image_index][0][:, :, channel_index]

# create animated plot
fig = go.Figure(
data=[go.Heatmap(z=z0, showscale=False)],
layout=go.Layout(
    title="Timeframe video",
    updatemenus=[dict(
        type="buttons",
        buttons=[dict(label="Play",
                      method="animate",
                      args=[None])])]
),
frames=frames)
    
fig.show()